<a href="https://colab.research.google.com/github/gasgustavo/EDA_Cryptocurrencies/blob/main/Trabalho_final_AI.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd

from datetime import datetime
import numpy as np
import random
import plotly.graph_objs as go
import os

from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import PolynomialFeatures
from sklearn.neural_network import MLPRegressor
from sklearn.preprocessing import MinMaxScaler

In [ ]:
# Le todos os arquivos da pasta q sao csv
def load_data():
  df = pd.DataFrame()
  for arquivo in os.listdir():
    if arquivo.endswith('.csv'):
      df = df.append(pd.read_csv(arquivo, skiprows=1))
  return df
df = load_data()

In [ ]:
symbols = df.symbol.unique()
','.join([i.split('/')[0] for i in symbols.tolist()])

'ZRX,BTC,EOS,ETC,DASH,REP,LSK,XRP,LTC,ETH'

In [ ]:
# Formata data para date e ordena por symbol e date
df['date'] = df.date.apply(lambda x: datetime.strptime(x, '%Y-%m-%d %H:%M:%S').date())
df = df.sort_values(['symbol','date']).set_index('date')

# Visualização dos dados

In [ ]:
titulo = 'Evolução do preço no tempo'
fig = go.Figure()

for symbol in symbols:
  df_aux = df[df['symbol']==symbol]
  fig.add_trace(go.Scatter(x = df_aux.index, y=df_aux.close.values, name=symbol))
display(fig.update_layout(title=titulo))
titulo = 'Volatilidade no tempo'
fig = go.Figure()
for symbol in symbols:
  df_aux = df[df['symbol']==symbol]['close']
  fig.add_trace(go.Scatter(x = df_aux.index, y=(np.log(df_aux/df_aux.shift()).rolling(window=252).std() * np.sqrt(252)).values, name=symbol))
fig.update_layout(title=titulo)

In [ ]:
fig = go.Figure()
for symbol in symbols:
  fig = go.Figure()
  fig.add_trace(go.Histogram(x=df[df['symbol']==symbol]['close'].diff().values))
  display(fig.update_layout(title=f'Histograma de retorno bruto de {symbol}'))

**2 Desenvolver as seguintes análises nos dados de 10 criptomoedas.**
* Calcular a média
* Calcular o desvio padrão
* Fazer o box plot
* Fazer uma análise da variabilidade dessas criptomoedas
* Fazer gráfico de linha destacando a média, mediana e a moda

In [ ]:
# Calcular a média e desvio padrão

dict_metrics = {}
list_metrics_lines = ['Média','Desvio Padrão','Mediana','Moda']
for symbol in symbols:
  df_aux = df[df["symbol"]==symbol]
  dict_metrics[symbol.split("/")[0]] = {
      list_metrics_lines[0]: f'{round(df_aux.close.mean(),2)} USD', #Média
      list_metrics_lines[1]: f'{round(df_aux.close.std(),4)} USD', #Desvio Padrão
      list_metrics_lines[2]: f'{round(df_aux.close.median(),4)} USD', #Mediana
      list_metrics_lines[3]: f'{list(round(df_aux.close.mode(),4))}', #Moda
  }
pd.DataFrame(dict_metrics).T

Média  ...                                               Moda
ZRX       0.62 USD  ...  [0.2317, 0.2403, 0.2481, 0.3131, 0.32, 0.3204,...
BTC   11664.53 USD  ...                                            [233.0]
EOS       4.05 USD  ...                                    [2.526, 3.6644]
ETC      14.27 USD  ...                                             [51.8]
DASH    150.39 USD  ...                                         [3.7, 5.9]
REP      19.01 USD  ...                                             [10.0]
LSK       2.13 USD  ...                                            [1.049]
XRP       0.35 USD  ...                                           [0.0114]
LTC     192.19 USD  ...  [107.2675, 113.0712, 117.6682, 119.237, 119.51...
ETH     566.54 USD  ...                                            [11.32]

[10 rows x 4 columns]

In [ ]:
titulo = 'Boxplot'
fig = go.Figure()

for symbol in symbols:
  df_aux = df[df['symbol']==symbol]
  fig.add_trace(go.Box(y=df_aux.close.values, name=symbol))
display(fig.update_layout(title=titulo))

In [ ]:
#  Fazer gráfico de linha destacando a média, mediana e a moda ISRAEL

titulo = 'Gráfico de linha'
fig = go.Figure()

#list_metrics_lines
#dict_metrics[]

for symbol in symbols:
  df_aux = df[df['symbol']==symbol].reset_index()
  fig = go.Figure(data=[go.Scatter(x=df_aux.date, y=df_aux.close.values, line=dict(color="crimson"), name=symbol)])

  #dict_metrics[symbol.split("/")[0]][list_metrics_lines[0]] #['Média','Desvio Padrão','Mediana','Moda']
  """fig.add_shape(
      type="line",
      x0=df_aux.date.min, float(dict_metrics[symbol.split("/")[0]][list_metrics_lines[0]].split(" ")[0]), x1=df_aux.date.max, y1=float(dict_metrics[symbol.split("/")[0]][list_metrics_lines[0]].split(" ")[0]),
      line=dict(color="RoyalBlue",width=3,dash="dashdot")
  )"""
  mean = float(dict_metrics[symbol.split("/")[0]][list_metrics_lines[0]].split(" ")[0])
  fig.add_trace(
    go.Scatter(x = [df_aux.date[0],df_aux.date[len(df_aux.date)-1]],y = [mean,mean], name=list_metrics_lines[0], line=dict(color='orange', dash='dash')) 
  )
  """fig.add_shape(
    type="line",
    name = list_metrics_lines[0],
    x0=df_aux.date[0], y0=mean, x1=df_aux.date[len(df_aux.date)-1], y1=mean,
    line=dict(
        color="Orange",
        width=4,
        dash="dashdot",
    )
  )"""
  std_dev = float(dict_metrics[symbol.split("/")[0]][list_metrics_lines[1]].split(" ")[0])
  fig.add_trace(
    go.Scatter(x = [df_aux.date[0],df_aux.date[len(df_aux.date)-1]],y = [mean-std_dev,mean-std_dev], name="Média - " + list_metrics_lines[1], line=dict(color='LightSeaGreen', dash='dashdot')) 
  )
  fig.add_trace(
    go.Scatter(x = [df_aux.date[0],df_aux.date[len(df_aux.date)-1]],y = [mean+std_dev,mean+std_dev], name="Média + " + list_metrics_lines[1], line=dict(color='Blue', dash='dashdot')) 
  )
  """fig.add_shape(
    type="line",
    name = "Média +/- " + list_metrics_lines[1],
    x0=df_aux.date[0], y0=mean-std_dev, x1=df_aux.date[len(df_aux.date)-1], y1=mean-std_dev,
    line=dict(
        color="LightSeaGreen",
        width=4,
        dash="dashdot",
    )
  )
  fig.add_shape(
    type="line",
    x0=df_aux.date[0], y0=mean+std_dev, x1=df_aux.date[len(df_aux.date)-1], y1=mean+std_dev,
    line=dict(
        color="LightSeaGreen",
        dash="dashdot",
    )
  )"""
  median = float(dict_metrics[symbol.split("/")[0]][list_metrics_lines[2]].split(" ")[0])
  fig.add_trace(
    go.Scatter(x = [df_aux.date[0],df_aux.date[len(df_aux.date)-1]],y = [median,median], name=list_metrics_lines[2], line=dict(color='Violet', dash='dash')) 
  )
  """fig.add_shape(
    type="line",
    name = list_metrics_lines[2],
    x0=df_aux.date[0], y0=median, x1=df_aux.date[len(df_aux.date)-1], y1=median,
    line=dict(
        color="Violet",
        width=4,
        dash="dashdot",
    )
  )"""
  tmp=0
  for mode in list(np.array(dict_metrics[symbol.split("/")[0]][list_metrics_lines[3]][1:-1].split(", ")).astype(np.float))[:5]:
      fig.add_trace(
        go.Scatter(x = [df_aux.date[0],df_aux.date[len(df_aux.date)-1]],y = [mode,mode], name= str(tmp+1) + "ª " + list_metrics_lines[3], line=dict(color='Green', dash='dashdot')) 
      )
      tmp+=1
      

  display(fig.update_layout(title=titulo+" "+symbol.split("/")[0]))

**3** Pesquisar e escolher variáveis (features) de entrada para a sua rede. Você pode
usar dados externos (Ex: Relação da moeda com dólar, com real, indicadores
macro-econômicos, etc.), ou dados da própria série (média dos últimos 7 dias,
desvio padrão dos últimos 7 dias, correlação entre as moedas, etc.). Ou seja, você
deverá encontrar as melhores features que irá considerar para o seu modelo

In [ ]:
df = df.rename(columns={
    'Volume USDT': 'volume_usdt'
})
"""
  Escolhemos essas variáveis gráficas para entrada do modelo. 
  E para gerar um contexto temporal temos os valores de open, high, low, close e
  volume em dolares de 8 a 6 dias antes do dia previsto em questão.

"""
features = ['open', 'high', 'low', 'close', 'volume_usdt']
features

['open', 'high', 'low', 'close', 'volume_usdt']

**4.** Aplicar em seu treinamento a estratégia de validação K-fold cross validation

In [ ]:
TAMANHO_JANELA_DESLIZANTE = 6
DIAS_DE_ANTECIPACAO = 2

def create_x_y(DIAS_DE_ANTECIPACAO, TAMANHO_JANELA_DESLIZANTE):
  """
    Cria os dados de predição y e as features X para predicao do preço
    DIAS_DE_ANTECIPACAO é a quantidade de dias que iremos prever com 
    antecedencia
    TAMANHO_JANELA_DESLIZANTE é a quantidade de dias que olharemos do passado
    para cada feature

    return dict_data: dicionario cuja chave é o simbolo de cada moeda e 
    o valor é um dicionario com o X e o y dessa moeda
  """
  dict_data = {}
  for symbol,df_coin in df.groupby('symbol'):
    
    X = []
    y = []
    x = df_coin.dropna(subset=features)[features].reset_index(drop=True).values
    
    for i in range(TAMANHO_JANELA_DESLIZANTE+DIAS_DE_ANTECIPACAO+1,len(x)):
      sample = {}
      for k in range(1,TAMANHO_JANELA_DESLIZANTE+1):
        sample.update({
          f'd-{k+DIAS_DE_ANTECIPACAO}_close': x[i-k-DIAS_DE_ANTECIPACAO][0],
          f'd-{k+DIAS_DE_ANTECIPACAO}_high': x[i-k-DIAS_DE_ANTECIPACAO][1],
          f'd-{k+DIAS_DE_ANTECIPACAO}_open': x[i-k-DIAS_DE_ANTECIPACAO][2],
          f'd-{k+DIAS_DE_ANTECIPACAO}_low': x[i-k-DIAS_DE_ANTECIPACAO][3],
          f'd-{k+DIAS_DE_ANTECIPACAO}_volume_usdt': x[i-k-DIAS_DE_ANTECIPACAO][4]
        })
            
      X.append(sample)
      y.append(x[i][0])

    dict_data[symbol] = {
        'X': X,
        'y': y,
        'tempo': df_coin.index[DIAS_DE_ANTECIPACAO + TAMANHO_JANELA_DESLIZANTE+1:]
    }
  return dict_data
dict_data = create_x_y(DIAS_DE_ANTECIPACAO, TAMANHO_JANELA_DESLIZANTE)

Treinando o modelo para Bitcoin

In [ ]:
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score
from sklearn.metrics import r2_score

symbol = 'BTC/USDT'
X, y, tempo = dict_data[symbol]['X'], dict_data[symbol]['y'], dict_data[symbol]['tempo'] 


X = pd.DataFrame(X)
# Dividimos entre o dataset de treino e o dataset de teste
X_train, X_test, y_train, y_test = train_test_split(X,y, test_size=0.2)

In [ ]:
# Ecolhendo os melhores hiperparâmetros

possibles_hidden_layer_sizes = [
  (64), (128), (256), (512), 
  (64, 64), (128, 64), (256, 64), (512, 64), 
  (64, 128), (128, 128), (256, 128), (512, 128), 
  (64, 256), (128, 256), (256, 256), (512, 256), 
  (64, 512), (128, 512), (256, 512), (512, 512),
]
activations = {'identity', 'relu'}
learning_rates = {'constant', 'invscaling', 'adaptive'}
best_model = None
best_score = -np.inf
for hidden_layer_sizes in possibles_hidden_layer_sizes:
  for activation in activations:
    model = MLPRegressor(
        hidden_layer_sizes = hidden_layer_sizes,
        activation=activation,
        max_iter=1000,
        learning_rate ='adaptive',
        # verbose=2,
        learning_rate_init=0.1,
        random_state = 0
        )
    score = np.mean(cross_val_score(model, X_train, y_train, cv=3, n_jobs=-1, scoring='neg_median_absolute_error'))

    print('hidden_layer_sizes: {}, activation: {}, score: {}'.format(hidden_layer_sizes, activation, score))
    if score > best_score:
      best_score = score
      best_model = model.fit(X=X_train.values,y=y_train)

hidden_layer_sizes: 64, activation: identity, score: -160.9864958140962
hidden_layer_sizes: 64, activation: relu, score: -184.1279566414171
hidden_layer_sizes: 128, activation: identity, score: -151.04462824068915
hidden_layer_sizes: 128, activation: relu, score: -167.9221193652916
hidden_layer_sizes: 256, activation: identity, score: -144.10437477393188
hidden_layer_sizes: 256, activation: relu, score: -149.10157077737807
hidden_layer_sizes: 512, activation: identity, score: -144.31303854084354
hidden_layer_sizes: 512, activation: relu, score: -251.22853705157135
hidden_layer_sizes: (64, 64), activation: identity, score: -152.64521790450104
hidden_layer_sizes: (64, 64), activation: relu, score: -266.32954164327066
hidden_layer_sizes: (128, 64), activation: identity, score: -146.42018419150008
hidden_layer_sizes: (128, 64), activation: relu, score: -187.93584427250047
hidden_layer_sizes: (256, 64), activation: identity, score: -174.6439628982213
hidden_layer_sizes: (256, 64), activatio

In [ ]:
# Testando em dados nao vistos pelo modelo
y_pred_mlp = best_model.predict(X_test)
display('Parametros:', best_model.get_params())
r2_score(y_test, y_pred_mlp)

'Parametros:'

{'activation': 'identity',
 'alpha': 0.0001,
 'batch_size': 'auto',
 'beta_1': 0.9,
 'beta_2': 0.999,
 'early_stopping': False,
 'epsilon': 1e-08,
 'hidden_layer_sizes': 256,
 'learning_rate': 'adaptive',
 'learning_rate_init': 0.1,
 'max_fun': 15000,
 'max_iter': 1000,
 'momentum': 0.9,
 'n_iter_no_change': 10,
 'nesterovs_momentum': True,
 'power_t': 0.5,
 'random_state': 0,
 'shuffle': True,
 'solver': 'adam',
 'tol': 0.0001,
 'validation_fraction': 0.1,
 'verbose': False,
 'warm_start': False}

0.9961780164927178

In [ ]:
titulo ='Dados de preço Real vs Predição - {}'.format(symbol)
fig = go.Figure()
y_pred_mlp = best_model.predict(X)
fig.add_trace(go.Scatter(x = tempo, y=y, name='Real'))
fig.add_trace(go.Scatter(x = tempo, y=y_pred_mlp, name='Predição'))

display(fig.update_layout(title=titulo))

**5.** Computar o lucro obtido com seu modelo, caso tenha investido U$ 1,000.00 no
primeiro dia de operação, refazendo investimentos de todo o saldo acumulado
diariamente, caso a previsão do valor de fechamento do próximo dia seja superior ao
do dia atual. Comparar seu modelo MLP com modelo de regressão (linear, e
polinomial - graus 2 até 10):
* Diagrama de dispersão (com todos modelos)
* Definir os coeficientes de correlação dos regressores
* Determinar a equação que melhor representa os regressores
* Cálculo do erro padrão
* Cálculo do erro padrão entre o MLP e o melhor regressor
* Plotar um gráfico mostrando a evolução do lucro obtido em cada modelo

In [ ]:
def erro_padrao(y_true, y_pred, sample_weight=None):
  df = pd.DataFrame({'y_true':y_true,'y_pred':y_pred})
  df['y-yhat2'] = df.apply(lambda x: (x.y_true - x.y_pred)**2,axis=1) / (len(df) - 2)
  return df['y-yhat2'].sum()**0.5
  
def calcula_retorno(y, y_pred, dinheiro_inicial = 1000):
  def comprar_ativos(valor_do_ativo, dinheiro):
    qtd_ativos_comprados = dinheiro//valor_do_ativo
    troco = dinheiro - (valor_do_ativo * qtd_ativos_comprados)
    return qtd_ativos_comprados, round(troco,2)

  def vender_ativo(valor_do_ativo, qtd_ativos):
    return valor_do_ativo*qtd_ativos
  
  dinheiro_na_carteira = dinheiro_inicial
  ativos_na_carteira = 0
  valor_predito_anterior = -1
  lista_poder_de_compra = [0]  

  for hoje, _ in enumerate(y[1:-1]):
    lista_poder_de_compra.append((dinheiro_na_carteira + ativos_na_carteira*y[hoje])-dinheiro_inicial)
    amanha = hoje +1
    # se preco aumentar comprar ativo
    if (y_pred[hoje] <  y_pred[amanha]) and (dinheiro_na_carteira> y_pred[hoje]):
      qtd_ativos_comprados, troco = comprar_ativos(valor_do_ativo=y[hoje], dinheiro=dinheiro_na_carteira)
      dinheiro_na_carteira = troco
      ativos_na_carteira += qtd_ativos_comprados
      # print('COMPRA: {} :::: {}'.format(dinheiro_na_carteira, ativos_na_carteira))

    # se preco diminuir vender ativo
    if (y_pred[hoje] >  y_pred[amanha]) and (ativos_na_carteira>0):
      dinheiro_de_venda = vender_ativo(valor_do_ativo=y[hoje], qtd_ativos=ativos_na_carteira)
      dinheiro_na_carteira += dinheiro_de_venda
      ativos_na_carteira = 0
      # print('VENDA: {} :::: {}'.format(dinheiro_na_carteira, ativos_na_carteira))
  if ativos_na_carteira>0:
    dinheiro_na_carteira += vender_ativo(valor_do_ativo=y[hoje+1], qtd_ativos=ativos_na_carteira)
  lista_poder_de_compra.append((dinheiro_na_carteira + ativos_na_carteira*y[hoje])-dinheiro_inicial)
  return dinheiro_na_carteira, lista_poder_de_compra



In [ ]:
# Calculamos modelo de regressão linear e polinomial (graus 2 a 10)

dinheiro_inicial = 1000

y_pred_regressao = []
retorno_predicao_regressao = [None] * 10
lista_poder_de_compra_regressao = [None] * 10

"""lm_model = LinearRegression()
y_pred_regressao[0] = lm_model.fit(y)
retorno_predicao_regressao[0], lista_poder_de_compra_regressao[0] = calcula_retorno(y, y_pred_regressao[i], dinheiro_inicial)"""

#ntempo = np.array([x.days for x in np.diff(tempo)]).cumsum()
#ntempo = np.insert(ntempo,0,0,axis=0)

ntempo = np.array((tempo - tempo[0]).days)
coef_list = []
y = np.nan_to_num(y)
for i in range(0,10):
  c, _, _, coef, _ = np.polyfit(ntempo, y, i+1, full=True)
  coef_list.append([round(i,3) for i in coef])
  poly_tmp = np.poly1d(c)
  y_pred_regressao.append(poly_tmp(ntempo))
  #y_pred_regressao[i] = poly.fit_transform(y)
  retorno_predicao_regressao[i], lista_poder_de_compra_regressao[i] = calcula_retorno(y, y_pred_regressao[i], dinheiro_inicial)




In [ ]:
titulo ='Gráfico de dispersão. Modelos de Regressão vs Real - {}'.format(symbol)
fig = go.Figure()

fig.add_trace(go.Scatter(x = tempo, y=y, name='Valor real', mode='markers'))
fig.add_trace(go.Scatter(x = tempo, y=y_pred_mlp, name='Valor previsto MLP', ))

for i in range(len(lista_poder_de_compra_regressao)):
  fig.add_trace(go.Scatter(x = tempo, y=y_pred_regressao[i], name='Valor previsto no modelo de regressão de grau ' + str(i+1)))
display(fig.update_layout(title=titulo))

In [ ]:
print('Erro padrão do MLP: {}'.format(erro_padrao(y, y_pred_mlp)))

Erro padrão do MLP: 985.8101046970781


In [ ]:
pd.set_option('display.max_colwidth', None)

df_regressores = pd.DataFrame({
    'Grau': [i+1 for i in range(len(coef_list))], 
    'Coeficientes': coef_list,
    'Erro padrão': [ erro_padrao(y,i) for i in y_pred_regressao]
})
df_regressores.set_index('Grau')

Coeficientes   Erro padrão
Grau                                                                                     
1                                                            [1.368, 0.358]  10515.882825
2                                                     [1.655, 0.504, 0.091]   8310.371053
3                                                [1.9, 0.607, 0.148, 0.019]   7202.231342
4                                       [2.118, 0.688, 0.197, 0.035, 0.004]   6814.579518
5                                [2.317, 0.755, 0.239, 0.051, 0.008, 0.001]   6726.687746
6                           [2.502, 0.813, 0.277, 0.067, 0.012, 0.002, 0.0]   5995.900629
7                      [2.674, 0.864, 0.311, 0.082, 0.017, 0.003, 0.0, 0.0]   5427.682945
8               [2.836, 0.911, 0.342, 0.097, 0.022, 0.004, 0.001, 0.0, 0.0]   4972.341081
9            [2.99, 0.953, 0.37, 0.111, 0.027, 0.005, 0.001, 0.0, 0.0, 0.0]   4505.209292
10    [3.137, 0.993, 0.397, 0.125, 0.032, 0.007, 0.001, 0.0, 0.0, 0.0, 0.0]   4488.639869

In [ ]:
y_pred_regressao

[array([-9183.14164565, -8987.15356311, -8970.8212229 , ...,
        29655.16337794, 29671.49571815, 29687.82805836]),
 array([ 6129.80541867,  5887.77729276,  5867.79932403, ...,
        40850.00816939, 40899.56940142, 40949.16002449]),
 array([-5912.76583232, -5467.81505013, -5431.30682226, ...,
        48945.9431286 , 49045.40868108, 49145.01494518]),
 array([ 2012.27606699,  1718.03880078,  1694.43031663, ...,
        54214.33619154, 54366.95543211, 54519.92813414]),
 array([ 6266.64928132,  5394.64056524,  5324.68001415, ...,
        51408.09032176, 51519.9681372 , 51631.94640846]),
 array([-7270.67434699, -5660.54219969, -5534.59726443, ...,
        42934.30084419, 42879.56157787, 42823.43621836]),
 array([ 5532.53124501,  4132.9048091 ,  4025.8203738 , ...,
        35567.43512533, 35321.74330938, 35072.33829618]),
 array([-6786.97133033, -4615.78822878, -4452.47005704, ...,
        29018.17258638, 28553.56277871, 28081.75356479]),
 array([ 6542.36674483,  4098.7865586 ,  3921.32

In [ ]:
print('Erro padrão entre regressor de grau 10 e MLP: {}'.format(erro_padrao(y_pred_mlp, y_pred_regressao[9])))

Erro padrão entre regressor de grau 10 e MLP: 4464.542700537212


In [ ]:
# Calculamos o retorno pra mlp
retorno_predicao_mlp, lista_poder_de_compra_mlp = calcula_retorno(y, y_pred_mlp, dinheiro_inicial)

# Estrategia buy and hold
buy_and_hold = dinheiro_inicial//y[0] * y[-1]

In [ ]:
titulo ='Retorno acumulado no tempo - {}'.format(symbol)
fig = go.Figure()
y_pred = best_model.predict(X)
fig.add_trace(go.Scatter(x = tempo, y=lista_poder_de_compra_mlp, name='Retorno acumulado MLP'))

# Adicionando os dados das regressões
for i in range(len(lista_poder_de_compra_regressao)):
  fig.add_trace(go.Scatter(x = tempo, y=lista_poder_de_compra_regressao[i], name='Retorno acumulado regressão de grau ' + str(i+1)))

# fig.add_trace(go.Scatter(x = tempo, y=[buy_and_hold]*len(tempo), name='Buy and Hold'))




display(fig.update_layout(title=titulo))

**6.** Crie uma função em Python que, com nível de significância de 5%, construa um
teste de hipótese analisando se o retorno esperado médio será superior ou igual à
x% (a ser definido pelo usuário) baseado na amostra que você utilizou. Realize esta
análise para todas as criptomoedas do dataset.

In [ ]:
from scipy.stats import norm,t

def teste_hipotese(percentual, alpha=0.05, verbose=0):
  
  possible_coins = []

  # Iteramos as moedas
  for symbol, dict_aux in dict_data.items():
    y = np.array(dict_data[symbol]['y'])
    distribuicao = y[1:]/y[:-1]
    media_pop = np.mean(distribuicao)
    n = len(distribuicao)
    std = np.std(distribuicao)
    media_esperada = (percentual/100)+1 # Media imputada

    # Encontramos z tabelado com a distribuição normal se n>=30 e com a de student caso contrário
    ztab = 0.0
    if n >= 30:
      ztab = norm.ppf(1 - alpha) # a função retorna P(Z < z)
    else:
      ztab = t.ppf(1 - alpha, n - 1) # a função retorna P(T < t)

    zcalc = (media_pop - media_esperada)/(std/(n**0.5))

    if verbose==2:
      print("{} zcalc:{} ztab:{}".format(symbol,zcalc, ztab))
      print("{} media_pop:{} std:{}".format(symbol,media_pop, std))
    if zcalc > ztab:
      possible_coins.append(symbol.split('/')[0])
  return sorted(possible_coins)

In [ ]:
#teste_hipotese(0.4,verbose=2)

BTC/USDT zcalc:-1.2033301278593782 ztab:1.6448536269514722
BTC/USDT media_pop:1.0029930153530824 std:0.042332430275911055
DASH/USDT zcalc:1.4635226087500923 ztab:1.6448536269514722
DASH/USDT media_pop:1.0621156760040762 std:1.9514275210507508
EOS/USDT zcalc:-0.5841169216147799 ztab:1.6448536269514722
EOS/USDT media_pop:1.0027614557848956 std:0.07541487059908819
ETC/USDT zcalc:0.290933629256691 ztab:1.6448536269514722
ETC/USDT media_pop:1.0045140191987147 std:0.0795645097246931
ETH/USDT zcalc:1.078505735580624 ztab:1.6448536269514722
ETH/USDT media_pop:1.0054996251426804 std:0.06772010089264263
LSK/USDT zcalc:-0.12908395173139628 ztab:1.6448536269514722
LSK/USDT media_pop:1.003690310023346 std:0.0835230234482003
LTC/USDT zcalc:0.04511303206904633 ztab:1.6448536269514722
LTC/USDT media_pop:1.0041878528991248 std:0.08149205538130587
REP/USDT zcalc:-0.4777814081483824 ztab:1.6448536269514722
REP/USDT media_pop:1.0030981692086656 std:0.07285996319346531
XRP/USDT zcalc:1.7843668843317384 zta

['XRP']